In [1]:
import string
import re
from pickle import dump
from unicodedata import normalize
from numpy import array

In [2]:
from pickle import load
from numpy import array
from numpy import argmax
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import load_model
from nltk.translate.bleu_score import corpus_bleu

Using TensorFlow backend.


In [3]:
INDIC_NLP_LIB_HOME=r"/home/simran/NLP Applications/nla_project/indic_nlp_library"
INDIC_NLP_RESOURCES=r"/home/simran/NLP Applications/nla_project/indic_nlp_resources"

In [4]:
import sys
sys.path.append(r'{}/src'.format(INDIC_NLP_LIB_HOME))
sys.path.append(r'/home/simran/NLP Applications/nla_project/hindi-tokenizer')

In [5]:
from indicnlp import common
common.set_resources_path(INDIC_NLP_RESOURCES)

In [6]:
from indicnlp import loader
loader.load()

/home/simran/NLP Applications/nla_project/indic_nlp_library/src/indicnlp/script/indic_scripts.py:116: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ALL_PHONETIC_VECTORS= ALL_PHONETIC_DATA.ix[:,PHONETIC_VECTOR_START_OFFSET:].as_matrix()
/home/simran/NLP Applications/nla_project/indic_nlp_library/src/indicnlp/script/indic_scripts.py:117: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  TAMIL_PHONETIC_VECTORS=TAMIL_PHONETIC_DATA.ix[:,PHONETIC_VECTOR_START_OFFSET:].as_matrix()
/home/simran/NLP Applications/nla_project/indic_nlp_library/src/indicnlp/script/english_script.py:113: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  ENGLISH_PHONETIC_VECTORS=ENGLISH_PHONETIC_DATA.ix[:,PHONETIC_VECTOR_START_OFFSET:].as_matrix()


In [7]:
from indicnlp.normalize.indic_normalize import DevanagariNormalizer
factory = DevanagariNormalizer()

In [8]:
from indicnlp.tokenize import indic_tokenize  

In [9]:
# load doc into memory
def load_doc(filename):
    # open the file as read only
    file = open(filename, mode='rt', encoding='utf-8')
    # read all text
    text = file.read()
    # close the file
    file.close()
    return text

In [10]:
text = load_doc('data/eng-hindi.txt')

In [11]:
#text

In [12]:
# split a loaded document into sentences
def to_pairs(doc):
    lines = doc.strip().split('\n')
    pairs = [line.split('\t') for line in  lines]
    return pairs

In [13]:
pairs = to_pairs(text)
#pairs

In [14]:
def clean_text(line):
    text = line
    text=text.replace(u',','')
    text=text.replace(u'"','')
    text=text.replace(u'(','')
    text=text.replace(u')','')
    text=text.replace(u'"','')
    text=text.replace(u':','')
    text=text.replace(u"'",'')
    text=text.replace(u"‘‘",'')
    text=text.replace(u"’’",'')
    text=text.replace(u"''",'')
    text=text.replace(u".",'')
    text=text.replace(u"-",'')
    text=text.replace(u"।",'')
    text=text.replace(u"?",'')
    text=text.replace(u"‘",'')
    text=text.replace(u"+",'')
    text=text.replace(u"%",'')
    text=text.replace(u"…",'')
    text=text.replace(u"”",'')
    text=text.replace(u"\\",'')
    text=text.replace(u"_",'')
    text=text.replace(u"[",'')
    text=text.replace(u"]",'')
    text=re.sub('[a-zA-Z]', '', text)
    text=re.sub('[0-9+\-*/.%>=!;~{}×–`’]', '', text)
    return text

In [15]:
# clean a list of lines
def clean_pairs(lines):
    cleaned = list()
    # prepare regex for char filtering
    re_print = re.compile('[^%s]' % re.escape(string.printable))
    # prepare translation table for removing punctuation
    table = str.maketrans('', '', string.punctuation)
    for pair in lines:
        clean_pair = list()
        
        line = pair[0]
        #print (line)
        line = normalize('NFD', line).encode('ascii', 'ignore')
        line = line.decode('UTF-8')
        line = line.split()
        line = [word.lower() for word in line]
        line = [word.translate(table) for word in line]
        line = [re_print.sub('', w) for w in line]
        line = [word for word in line if word.isalpha()]
        clean_pair.append(' '.join(line))
        
        line = pair[1]
        #print (line)
        line = factory.normalize(line)
        line = clean_text(line)
        tokens = list()
        for t in indic_tokenize.trivial_tokenize(line): 
            tokens.append(t)
        line = tokens
        line = [word.lower() for word in line]
        line = [word for word in line if not re.search(r'\d', word)]
        clean_pair.append(' '.join(line))
        
        print (clean_pair)
        
        cleaned.append(clean_pair)
    return array(cleaned)

In [16]:
clean_pairs = clean_pairs(pairs)
clean_pairs

['fresh breath and shining teeth enhance your personality', 'ताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं']
['your selfconfidence also increases with teeth', 'दाँतों से आपका आत्मविश्वास भी बढ़ता है']
['bacteria stay between our gums and teeth', 'हमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं']
['they make teeth dirty and breath stinky', 'ये दाँतों को गंदा और साँसों को बदबूदार बना देते हैं']
['you may keep your teeth clean and breath fresh by the help of some easy tips given here', 'यहाँ दिए कुछ आसान नुस्खों की मदद से आप अपने दाँतों को स्वच्छ और साँसों को ताजा रख सकते हैं']
['clean your teeth properly', 'दाँतों को ठीक से साफ करें']
['it takes two to three minutes to clean your teeth properly', 'दाँतों को ठीक से साफ करने में दो से तीन मिनट का समय लगता है']
['but most of the people give less than one minute for this', 'लेकिन ज्यादातर लोग इसके लिए एक मिनट से भी कम समय देते हैं']
['drink plenty of water', 'खूब पानी पीएँ']
['bacteria attack fast if the mouth dries up'

['treatment in tuberculosis is now done through the dots strategy', 'क्षय रोग के इलाज में अब डाट्स पद्धति से उपचार किया जाता है']
['in dots strategy patient is administered medicines under the direct care of the health workers', 'डाट्स पद्धति में रोगी को स्वास्थ्य कार्यकर्त्ताओं की सीधी देख रेख में दवा खिलाई जाती है']
['which is called dots lrb directly observed treatment with short course chemotherapy rrb', 'जिसे डाट्स डायरेक्टली आबजर्ब्ड ट्रीटमेंट विद सार्ट कोर्स कीमोथेरपी कहते हैं']
['as is revealed from the name directly observed treatment with short course chemotherapy means that patient takes short courses of antituberculosis drugs in presence of health worker', 'जैसा कि नाम से पता चलता है डायरेक्टली आबजर्ब्ड ट्रीटमेंट विद कोर्स कीमोथेरपी डाट्स का अर्थ है कि रोगी स्वास्थ्य कार्यकर्त्ता की उपस्थिति में एन्टी टीबी ड्रग्ज का शार्ट कोर्स लेता है']
['there are two stages in the treatment of tuberculosis', 'टीबी के उपचार में दो चरण होते हैं']
['intensive phase which goes on for months'

['but the number of patients coming to the psychiatrist and psychologists today has increased much than earlier', 'पर पहले की बनिस्पत आज सायकियाट्रिस्ट या सायकोलाजिस्टों के पास आनेवाले मरीजों की संख्या काफी बढ़ गई है']
['the advice of the psychologists is proving ineffective and modern medicines which suppress the symptoms of the problem are delivering more harm', 'मनोवैज्ञानिकों के मशविरे बेअसर साबित हो रहे हैं और समस्या के लक्षणों को दबाने का काम करनेवाली आधुनिक दवाएँ फायदे के बजाय नुकसान ज्यादा पहुँचा रही हैं']
['in the pomp of multimillion advertisements of modern medical science perhaps very few people will accept the truth that methods of effective treatment of common mental problems and severe psychological disorders are present in the ancient indian medical science that is ayurveda', 'मॉडर्न मेडिकल साइंस के बहुकरोड़ी विज्ञापनों के जोरशोर में बहुत कम लोग शायद इस सच को स्वीकार करें कि प्राचीन भारतीय चिकित्सा विज्ञान यानी आयुर्वेद में आम मानसिक समस्याओं व गंभीर मनोरोगों के इलाज के

['left hemisphere language lrb speaking cognizing the meaning of the words written and heard rrb maths analysis of problems estimation of time', 'बायाँ हेमीस्फीयर भाषा बोलना लिखे और सुने शब्दों का अर्थ समझना गणित समस्याओं का विश्लेषण समय का अनुमान']
['right hemisphere geometry painting instrumental music organization of facts estimation of space', 'दायाँ हेमीस्फीयर ज्यामिति ज्योमैट्री चित्रकला वाद्य संगीत तथ्यों का संयोजन स्थान का अनुमान']
['whatever we study in class generally gets accumulated in the right or left hemisphere according to this area division', 'साधारणतया हम क्लास में जो कुछ पढ़ते हैं वह इस क्षेत्र विभाजन के अनुसार दायें या बायें हेमीस्फीयर में संचित हो जाता है']
['but because of being connected with corpus callosum the knowledge of one is always available for the other when needed', 'परन्तु कोरपसकेलोसम से जुड़े होने के कारण एक या ज्ञान आवश्यकता पड़ने पर दूसरे के लिए सदा उपलब्ध रहता है']
['on the contrary the matter of the patients of roger sperry is in fact indeed exqui

['in cases were registered in the whole world out of which cases were found in india', 'में पूरे विश्व में केस दर्ज किए गए जिसमें से भारत में पाए गए']
['it is known that because of the increase of the cases of polio in india it has to face criticism from those countries of the world who have eradicated the disease of polio within them', 'ज्ञातब्य है कि पोलियो के मामलों में वृद्धि होने से भारत को विश्व के उन देशों में आलोचना का शिकार होना पड़ा है जिन्होंने अपने यहाँ पोलियो रोग का सफाया कर दिया है']
['according to the ministry of the centre for family welfare the virus of polio has now become limited to some selected districts of uttar pradesh and bihar', 'केन्द्रीय परिवार कल्याण मंत्रालय के अनुसार उत्तर प्रदेश और बिहार में भी पोलियो का वायरस अब कुछ चुनिंदा जिलों तक ही सीमित रह गया है']
['because the virus of polio is found only in the body of human beings its complete eradication is possible', 'पोलियो के विषाणु का केवल मानव शरीर में पाये जाने के कारण इसका जड़ से उन्मूलन संभव है']
['for 

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['here in guest houses you will find from double bedroom of fare three hundred rupees daily to rs daily in big hotels', 'यहाँ गेस्ट हाउसों में तीन सौ रुपये दैनिक किराये के डबल बेडरूम से लेकर बड़ी होटल में रु रोजाना तक के कमरे मिल जाएँगे']
['but to stay here in guest houses attached to homes is not only economical but also introduces to laddakhi culture and life style', 'लेकिन यहाँ घरों से जुड़े गेस्ट हाउसों में रहना न केवल किफ़ायती है बल्कि लद्दाखी संस्कृति व रहनसहन से परिचित भी कराता है']
['in the tourist season from june to september to get hotel booking done beforehand is always safe', 'जून से सिंतबर के टूरिस्ट सीजन में होटल बुकिंग पहले से करा लेना सुरक्षित रहता है']
['during mornings and evenings yearlong warm clothes have to be worn', 'सुबह व शाम के समय तो यहाँ पूरे सालभर गरम कपड़े पहनने होते हैं']
['from june to september there is a little warmth during day', 'जून से सितंबर तक दिन में थोड़ी गरमी होती है']
['although in august only there is a dip in day temperature', 'हालाँकि अगस

['even today there is a special attraction and a deep attachment towards these fairs in the citizens of the country and abroad', 'आज भी देश विदेश के नागरिकों में इन मेलों के प्रति एक विशेष आकर्षण एवं गहरा लगाव है']
['therefore seeing their popularity they should be encouraged', 'अतः इनकी लोकप्रियता को देखकर इन्हें प्रोत्साहित किया जाना चाहिए']
['the fondness of the tour of historical buildings ancient temples stupas and gumbad of historical importance is regularly increasing in the tourists of the country and abroad', 'देश विदेश के पर्यटकों में पुरातन महत्त्व की ऐतिहासिक इमारतों प्राचीन मंदिरों स्तूपों एवं गुम्बदों के भ्रमण का शौक लगातार बढ़ता जा रहा है']
['our country is an alive large museum of ruins relics and historical buildings of ancient indian culture', 'हमारा देश प्राचीन भारतीय सभ्यता के खण्डहरों मूर्तियों अवशेषों एवं ऐतिहासिक इमारतों का एक जीता जागता विशाल संग्रहालय है']
['giving it sufficient conservation one should give special attention to its care', 'इन्हें पर्याप्त संरक्

['in ankleshwar near bharuch oil is drilled due to which bharuch once again has become an important city', 'भरूच के पास अंकलेश्वर में तेल निकलता है जिसके कारण भरूच फिर एक बार महत्त्वपूर्ण शहर बन गया है']
['in bharuch district on the bank of narmada river ther eis a pilgrimage with the name of shuklateertha', 'भरूच जिले में नर्मदा नदी के किनारे शुक्लतीर्थ नाम का एक तीर्थस्थान है']
['near that only there is a huge banyan tree which is called kabeerbadh', 'उसी के पास एक बहुत ही बड़ा बड़ का पेड़ है जिसे कबीरबड़ कहते हैं']
['ahead of bharuch dakor city of kheda district is also considered as a big pilgrimage', 'भरूच से आगे खेड़ा जिले का डाकोर नगर भी बड़ा तीर्थस्थान माना जाता है']
['one devotee had made by bringing idol of shree krishn here from dwarka', 'एक भक्त ने द्वारका से श्रीकृष्ण की मूर्ति यहाँ लाकर बनाया था']
['on the day of every sharad poornima a big fair is held in dakor', 'प्रत्येक शरद पूर्णिमा के दिन डाकोर में बड़ा मेला लगता है']
['thousands of travellers take part in this fair'

array([['fresh breath and shining teeth enhance your personality',
        'ताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं'],
       ['your selfconfidence also increases with teeth',
        'दाँतों से आपका आत्मविश्वास भी बढ़ता है'],
       ['bacteria stay between our gums and teeth',
        'हमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं'],
       ...,
       ['i slowly said no', 'मैंने धीरे से कहा नहीं'],
       ['there was no permission to take bike inside the park',
        'पार्क में बाइक ले जाने की अनुमति नहीं थी'],
       ['somebody advised us that we should take safari for inside',
        'हमें किसी ने सलाह दी कि आप अंदर के लिए सफारी ले लो']],
      dtype='<U547')

In [17]:
# save a list of clean sentences to file
def save_clean_data(sentences, filename):
    dump(sentences, open(filename, 'wb'))
    print('Saved: %s' % filename)

In [18]:
save_clean_data(clean_pairs, 'clean_english-hindi.pkl')

Saved: clean_english-hindi.pkl


In [19]:
# spot check
for i in range(100):
    print('[%s] => [%s]' % (clean_pairs[i,0], clean_pairs[i,1]))

[fresh breath and shining teeth enhance your personality] => [ताजा साँसें और चमचमाते दाँत आपके व्यक्तित्व को निखारते हैं]
[your selfconfidence also increases with teeth] => [दाँतों से आपका आत्मविश्वास भी बढ़ता है]
[bacteria stay between our gums and teeth] => [हमारे मसूढ़ों और दाँतों के बीच बैक्टीरिया मौजूद होते हैं]
[they make teeth dirty and breath stinky] => [ये दाँतों को गंदा और साँसों को बदबूदार बना देते हैं]
[you may keep your teeth clean and breath fresh by the help of some easy tips given here] => [यहाँ दिए कुछ आसान नुस्खों की मदद से आप अपने दाँतों को स्वच्छ और साँसों को ताजा रख सकते हैं]
[clean your teeth properly] => [दाँतों को ठीक से साफ करें]
[it takes two to three minutes to clean your teeth properly] => [दाँतों को ठीक से साफ करने में दो से तीन मिनट का समय लगता है]
[but most of the people give less than one minute for this] => [लेकिन ज्यादातर लोग इसके लिए एक मिनट से भी कम समय देते हैं]
[drink plenty of water] => [खूब पानी पीएँ]
[bacteria attack fast if the mouth dries up] 

In [20]:
len(clean_pairs)

49999

In [21]:
print('[%s] => [%s]' % (clean_pairs[24999,0], clean_pairs[24999,1]))

[your hair will become beautiful black dense from its regular use] => [इसके नियमित इस्तेमाल से आपके बाल खूबसूरत काले घने हो जाएँगे]


# Code of ten minute sequence starts from here

In [22]:
lines = clean_pairs
lines = lines[:45000, :]
len(lines)

45000

In [23]:
num_samples = 50000
num_samples

50000

In [24]:
input_texts = []
target_texts = []
input_characters = set()
target_characters = set()

In [25]:
for line in lines:
    temp = line[0] + "\t" + line[1]
    #print (a)
    line = temp
    input_text, target_text = line.split('\t')
    target_text = '\t' + target_text + '\n'
    input_texts.append(input_text)
    target_texts.append(target_text)
    for char in input_text:
        if char not in input_characters:
            input_characters.add(char)
    for char in target_text:
        if char not in target_characters:
            target_characters.add(char)

In [26]:
print (len(input_texts))

45000


In [27]:
print (len(target_texts))

45000


In [28]:
input_characters

{' ',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z'}

In [29]:
target_characters

{'\t',
 '\n',
 ' ',
 'ँ',
 'ं',
 'ः',
 'अ',
 'आ',
 'इ',
 'ई',
 'उ',
 'ऊ',
 'ऋ',
 'ऍ',
 'ऎ',
 'ए',
 'ऐ',
 'ऑ',
 'ऒ',
 'ओ',
 'औ',
 'क',
 'ख',
 'ग',
 'घ',
 'ङ',
 'च',
 'छ',
 'ज',
 'झ',
 'ञ',
 'ट',
 'ठ',
 'ड',
 'ढ',
 'ण',
 'त',
 'थ',
 'द',
 'ध',
 'न',
 'प',
 'फ',
 'ब',
 'भ',
 'म',
 'य',
 'र',
 'ल',
 'ळ',
 'व',
 'श',
 'ष',
 'स',
 'ह',
 '़',
 'ा',
 'ि',
 'ी',
 'ु',
 'ू',
 'ृ',
 'ॄ',
 'ॅ',
 'े',
 'ै',
 'ॉ',
 'ॊ',
 'ो',
 'ौ',
 '्',
 'ॠ',
 '॥',
 'ਖ',
 'ਤ'}

In [30]:
input_texts[155]

'avoid heavy hard to digest tea coffee tobacco intoxicating things and exciting element'

In [31]:
target_texts[155]

'\tभारी गरिष्ठ चाय काफी तंबाकू नशीले पदार्थ व उत्तेजक पदार्थों से परहेज करें\n'

In [32]:
input_characters = sorted(list(input_characters))
target_characters = sorted(list(target_characters))
num_encoder_tokens = len(input_characters)
num_decoder_tokens = len(target_characters)
max_encoder_seq_length = max([len(txt) for txt in input_texts])
max_decoder_seq_length = max([len(txt) for txt in target_texts])

print('Number of samples:', len(input_texts))
print('Number of unique input tokens:', num_encoder_tokens)
print('Number of unique output tokens:', num_decoder_tokens)
print('Max sequence length for inputs:', max_encoder_seq_length)
print('Max sequence length for outputs:', max_decoder_seq_length)

Number of samples: 45000
Number of unique input tokens: 27
Number of unique output tokens: 75
Max sequence length for inputs: 547
Max sequence length for outputs: 497


In [33]:
print(input_characters)

[' ', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [34]:
print(target_characters)

['\t', '\n', ' ', 'ँ', 'ं', 'ः', 'अ', 'आ', 'इ', 'ई', 'उ', 'ऊ', 'ऋ', 'ऍ', 'ऎ', 'ए', 'ऐ', 'ऑ', 'ऒ', 'ओ', 'औ', 'क', 'ख', 'ग', 'घ', 'ङ', 'च', 'छ', 'ज', 'झ', 'ञ', 'ट', 'ठ', 'ड', 'ढ', 'ण', 'त', 'थ', 'द', 'ध', 'न', 'प', 'फ', 'ब', 'भ', 'म', 'य', 'र', 'ल', 'ळ', 'व', 'श', 'ष', 'स', 'ह', '़', 'ा', 'ि', 'ी', 'ु', 'ू', 'ृ', 'ॄ', 'ॅ', 'े', 'ै', 'ॉ', 'ॊ', 'ो', 'ौ', '्', 'ॠ', '॥', 'ਖ', 'ਤ']


In [35]:
input_token_index = dict(
  [(char, i) for i, char in enumerate(input_characters)])
target_token_index = dict(
  [(char, i) for i, char in enumerate(target_characters)])

In [36]:
import numpy as np

encoder_input_data = np.zeros(
  (len(input_texts), max_encoder_seq_length, num_encoder_tokens),
  dtype='float32')
decoder_input_data = np.zeros(
  (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
  dtype='float32')
decoder_target_data = np.zeros(
  (len(input_texts), max_decoder_seq_length, num_decoder_tokens),
  dtype='float32')

In [37]:
encoder_input_data.shape

(45000, 547, 27)

In [38]:
decoder_input_data.shape

(45000, 497, 75)

In [39]:
for i, (input_text, target_text) in enumerate(zip(input_texts, target_texts)):
    for t, char in enumerate(input_text):
        encoder_input_data[i, t, input_token_index[char]] = 1.
    for t, char in enumerate(target_text):
        # decoder_target_data is ahead of decoder_input_data by one timestep
        decoder_input_data[i, t, target_token_index[char]] = 1.
        if t > 0:
            # decoder_target_data will be ahead by one timestep
            # and will not include the start character.
            decoder_target_data[i, t - 1, target_token_index[char]] = 1.

In [40]:
encoder_input_data[155].shape

(547, 27)

In [41]:
import keras, tensorflow
from keras.models import Model
from keras.layers import Input, LSTM, Dense
import numpy as np

In [42]:
batch_size = 64  # batch size for training
epochs = 100  # number of epochs to train for
latent_dim = 256  # latent dimensionality of the encoding space

In [43]:
encoder_inputs = Input(shape=(None, num_encoder_tokens))
encoder = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
encoder_states = [state_h, state_c]

In [44]:
decoder_inputs = Input(shape=(None, num_decoder_tokens))
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs,
                                     initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

In [45]:
model = Model(inputs=[encoder_inputs, decoder_inputs], 
              outputs=decoder_outputs)

In [46]:
model.compile(optimizer='rmsprop', loss='categorical_crossentropy')
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None, 27)     0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, None, 75)     0                                            
__________________________________________________________________________________________________
lstm_1 (LSTM)                   [(None, 256), (None, 290816      input_1[0][0]                    
__________________________________________________________________________________________________
lstm_2 (LSTM)                   [(None, None, 256),  339968      input_2[0][0]                    
                                                                 lstm_1[0][1]                     
          

In [47]:
model.fit([encoder_input_data, decoder_input_data], decoder_target_data,
          batch_size=batch_size,
          epochs=epochs,
          validation_split=0.2)
model.save('seq2seq_eng-hindi.h5')

Train on 36000 samples, validate on 9000 samples
Epoch 1/100
36000/36000 [==============================] - 2906s 81ms/step - loss: 0.4134 - val_loss: 0.3632
Epoch 2/100
36000/36000 [==============================] - 2863s 80ms/step - loss: 0.3280 - val_loss: 0.3293
Epoch 3/100
36000/36000 [==============================] - 2785s 77ms/step - loss: 0.2962 - val_loss: 0.3119
Epoch 4/100
36000/36000 [==============================] - 2792s 78ms/step - loss: 0.2754 - val_loss: 0.2989
Epoch 5/100
36000/36000 [==============================] - 2941s 82ms/step - loss: 0.2611 - val_loss: 0.2904
Epoch 6/100
36000/36000 [==============================] - 3023s 84ms/step - loss: 0.2510 - val_loss: 0.2828
Epoch 7/100
36000/36000 [==============================] - 3379s 94ms/step - loss: 0.2433 - val_loss: 0.2785
Epoch 8/100
36000/36000 [==============================] - 4038s 112ms/step - loss: 0.2371 - val_loss: 0.2746
Epoch 9/100
36000/36000 [==============================] - 5980s 166ms/step - 

KeyboardInterrupt: 

In [48]:
model.save('seq2seq_eng-hindi.h5')

/home/simran/.local/lib/python3.6/site-packages/keras/engine/network.py:877: UserWarning: Layer lstm_2 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_1/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_1/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  '. They will not be included '


In [49]:
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer='rmsprop', loss='categorical_crossentropy')
model.load_weights('seq2seq_eng-hindi.h5')

In [50]:
encoder_model = Model(encoder_inputs, encoder_states)

decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]

decoder_outputs, state_h, state_c = decoder_lstm(
  decoder_inputs, initial_state=decoder_states_inputs)
decoder_states = [state_h, state_c]
decoder_outputs = decoder_dense(decoder_outputs)

decoder_model = Model(
  [decoder_inputs] + decoder_states_inputs,
  [decoder_outputs] + decoder_states)

In [51]:
# reverse-lookup token index to turn sequences back to characters
reverse_input_char_index = dict(
  (i, char) for char, i in input_token_index.items())
reverse_target_char_index = dict(
  (i, char) for char, i in target_token_index.items())

In [66]:
def decode_sequence(input_seq):

    states_value = encoder_model.predict(input_seq)

    target_seq = np.zeros((1, 1, num_decoder_tokens))
    target_seq[0, 0, target_token_index['\t']] = 1.

    stop_condition = False
    decoded_sentence = ''
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict([target_seq] + states_value)
    
        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += sampled_char

        if (sampled_char == '\n' or len(decoded_sentence) > max_decoder_seq_length):
              stop_condition = True
      

        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.
    
        states_value = [h, c]
    
    return decoded_sentence

In [67]:
for seq_index in range(10):
    input_seq = encoder_input_data[seq_index: seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    print('-')
    print('Input sentence:', input_texts[seq_index])
    print('Decoded sentence:', decoded_sentence)

-
Input sentence: fresh breath and shining teeth enhance your personality
Decoded sentence: सामान्यतः स्वास्थ्य के लिए स्थापित किया गया है

-
Input sentence: your selfconfidence also increases with teeth
Decoded sentence: इसके अलावा मानसिक रोग के कारण होता है

-
Input sentence: bacteria stay between our gums and teeth
Decoded sentence: सामान्यतः समय के लिए किसी भी कारण होता है

-
Input sentence: they make teeth dirty and breath stinky
Decoded sentence: यहाँ के साथ ही स्थान पर है

-
Input sentence: you may keep your teeth clean and breath fresh by the help of some easy tips given here
Decoded sentence: सामान्य रोग के कारण होने वाली बात को सामान्य कारण होता है जिससे किसी भी कारण होता है

-
Input sentence: clean your teeth properly
Decoded sentence: सामान्यतः ही सामान्य से कम होता है

-
Input sentence: it takes two to three minutes to clean your teeth properly
Decoded sentence: इसके अलावा मानसिक रोग के कारण होता है

-
Input sentence: but most of the people give less than one minute for th

In [69]:
input_sentence = "how are you"
test_sentence_tokenized = np.zeros((1, max_encoder_seq_length, num_encoder_tokens), dtype='float32')
for t, char in enumerate(input_sentence):
    test_sentence_tokenized[0, t, input_token_index[char]] = 1.
print(input_sentence)
print(decode_sequence(test_sentence_tokenized))

how are you
सामान्य रोग होते हैं



In [78]:
val_input_texts = []
val_target_texts = []
line_ix = 46000
lines = clean_pairs
for line in lines[line_ix:line_ix+10]:
    a = line[0] + "\t" + line[1]
    line = a
    input_text, target_text = line.split('\t')
    val_input_texts.append(input_text)
    val_target_texts.append(target_text)

#print (len(val_input_texts))
#print (len(val_target_texts))

val_encoder_input_data = np.zeros(
  (len(val_input_texts), max([len(txt) for txt in val_input_texts]),
   num_encoder_tokens), dtype='float32')

for i, input_text in enumerate(val_input_texts):
    for t, char in enumerate(input_text):
        val_encoder_input_data[i, t, input_token_index[char]] = 1.

In [79]:
for seq_index in range(10):
    input_seq = val_encoder_input_data[seq_index: seq_index + 1]
    decoded_sentence = decode_sequence(input_seq)
    print('-')
    print('Input sentence:', val_input_texts[seq_index])
    print('Decoded sentence:', decoded_sentence[:-1])
    print('Ground Truth sentence:', val_target_texts[seq_index])

-
Input sentence: settled in the north direction from mumbai the bordi is a pleasant tourist spot
Decoded sentence: सामान्यतः समय के लिए किसी भी कारण होता है जिसके लिए किसी भी कारण होता है
Ground Truth sentence: मुंबई से उत्तर दिशा में बसा बोर्डी एक रमणीय पर्यटन स्थल हैं
-
Input sentence: the sea coast of hahanubordi is spread in about kms
Decoded sentence: पार्क में स्थित है जिसके अलावा मानसिक रोग है
Ground Truth sentence: हहाणूबोर्डी का सागर तट लगभग किमी में फैला हुआ है
-
Input sentence: this region is famous for sapodilla and other fruits
Decoded sentence: यह स्थान पर स्थित है जिसके अलावा मानसिक रोग है
Ground Truth sentence: यह प्रदेश चीकू तथा अन्य फलों के लिए प्रसिद्ध है
-
Input sentence: bordi residents are also famous for schools
Decoded sentence: सामान्यतः समय के लिए किसी भी कारण होता है
Ground Truth sentence: बोर्डी निवासी स्कूलों के लिए भी प्रसिद्ध है
-
Input sentence: the udwada place of the zoroastrian people can be seen from here
Decoded sentence: साथ ही स्थान पर स्थित है ज

In [72]:
max([len(txt) for txt in val_input_texts])

31

#from pickle import load
from pickle import dump
from numpy.random import rand
from numpy.random import shuffle
from numpy import array
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from keras.utils.vis_utils import plot_model
from keras.models import Sequential
from keras.layers import LSTM
from keras.layers import Dense
from keras.layers import Embedding
from keras.layers import RepeatVector
from keras.layers import TimeDistributed
from keras.callbacks import ModelCheckpoint

#load a clean dataset
def load_clean_sentences(filename):
    return load(open(filename, 'rb'))

#save a list of clean sentences to file
def save_clean_data(sentences, filename):
    dump(sentences, open(filename, 'wb'))
    print('Saved: %s' % filename)

#load dataset
raw_dataset = load_clean_sentences('clean_english-hindi.pkl')

#reduce dataset size

'''
delete the lower code later
'''

n_sentences = 10000
dataset = raw_dataset[:n_sentences, :]

train, test = dataset[:9000], dataset[9000:]

'''
Originally it should be like this
n_sentences = 49999
dataset = raw_dataset[:n_sentences, :]

train, test = dataset[:25000], dataset[25000:]
'''

shuffle(train)
shuffle(test)
shuffle(dataset)

print(len(train))
print(len(test))

save_clean_data(dataset, 'clean_english-hindi-both.pkl')
save_clean_data(train, 'clean_english-hindi-train.pkl')
save_clean_data(test, 'clean_english-hindi-test.pkl')

In [ ]:
# prepare english tokenizer
eng_tokenizer = create_tokenizer(dataset[:, 0])
eng_vocab_size = len(eng_tokenizer.word_index) + 1
eng_length = max_length(dataset[:, 0])
print('English Vocabulary Size: %d' % eng_vocab_size)
print('English Max Length: %d' % (eng_length))
eng_tokenizer

In [ ]:
print(eng_tokenizer.document_count)
print(eng_tokenizer.word_counts)
print(eng_tokenizer.word_index)
print(eng_tokenizer.word_docs)

#prepare german tokenizer
hindi_tokenizer = create_tokenizer(dataset[:, 1])
hindi_vocab_size = len(hindi_tokenizer.word_index) + 1
hindi_length = max_length(dataset[:, 1])
print('Hindi Vocabulary Size: %d' % hindi_vocab_size)
print('Hindi Max Length: %d' % (hindi_length))

In [ ]:
print(hindi_tokenizer.document_count)
print(hindi_tokenizer.word_counts)
print(hindi_tokenizer.word_index)
print(hindi_tokenizer.word_docs)

In [ ]:
trainX = encode_sequences(eng_tokenizer, eng_length, train[:, 0])
trainX

In [ ]:
trainY = encode_sequences(hindi_tokenizer, hindi_length, train[:, 1])
trainY

In [ ]:
trainY = encode_output(trainY, hindi_vocab_size)
trainY

In [ ]:
testX = encode_sequences(eng_tokenizer, eng_length, test[:, 0])
testX

In [ ]:
testY = encode_sequences(hindi_tokenizer, hindi_length, test[:, 1])
testY

In [ ]:
testY = encode_output(testY, hindi_vocab_size)
testY

model = define_model(eng_vocab_size, hindi_vocab_size, eng_length, hindi_length, 256)

model.compile(optimizer='adam', loss='categorical_crossentropy')

In [ ]:
#from keras.utils.vis_utils import plot_model
print(model.summary())
#plot_model(model, to_file='model.png', show_shapes=True)

In [ ]:
# fit model
filename = 'model.h5'
checkpoint = ModelCheckpoint(filename, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(trainX, trainY, epochs=30, batch_size=64, validation_data=(testX, testY), callbacks=[checkpoint], verbose=2)

In [ ]:
dataset = load_clean_sentences('clean_english-hindi-both.pkl')
train = load_clean_sentences('clean_english-hindi-train.pkl')
test = load_clean_sentences('clean_english-hindi-test.pkl')

# prepare english tokenizer
eng_tokenizer = create_tokenizer(dataset[:, 0])
eng_vocab_size = len(eng_tokenizer.word_index) + 1
eng_length = max_length(dataset[:, 0])

# prepare german tokenizer
hindi_tokenizer = create_tokenizer(dataset[:, 1])
hindi_vocab_size = len(hindi_tokenizer.word_index) + 1
hindi_length = max_length(dataset[:, 1])

# prepare data
trainX = encode_sequences(eng_tokenizer, eng_length, train[:, 0])
testX = encode_sequences(eng_tokenizer, eng_length, test[:, 0])

In [ ]:
# load model
model = load_model('model.h5')

In [ ]:
def word_for_id(integer, tokenizer):
    for word, index in tokenizer.word_index.items():
        if index == integer:
            return word
    return None

In [ ]:
# generate target given source sequence
def predict_sequence(model, tokenizer, source):
    prediction = model.predict(source, verbose=0)[0]
    integers = [argmax(vector) for vector in prediction]
    target = list()
    for i in integers:
        word = word_for_id(i, tokenizer)
        if word is None:
            break
        target.append(word)
    return ' '.join(target)

In [ ]:
# evaluate the skill of the model
def evaluate_model(model, tokenizer, sources, raw_dataset):
    actual, predicted = list(), list()
    for i, source in enumerate(sources):
        # translate encoded source text
        source = source.reshape((1, source.shape[0]))
        translation = predict_sequence(model, eng_tokenizer, source)
        raw_target, raw_src = raw_dataset[i]
        if i < 10:
            print('src=[%s], target=[%s], predicted=[%s]' % (raw_src, raw_target, translation))
        actual.append(raw_target.split())
        predicted.append(translation.split())
    # calculate BLEU score
    print('BLEU-1: %f' % corpus_bleu(actual, predicted, weights=(1.0, 0, 0, 0)))
    print('BLEU-2: %f' % corpus_bleu(actual, predicted, weights=(0.5, 0.5, 0, 0)))
    print('BLEU-3: %f' % corpus_bleu(actual, predicted, weights=(0.3, 0.3, 0.3, 0)))
    print('BLEU-4: %f' % corpus_bleu(actual, predicted, weights=(0.25, 0.25, 0.25, 0.25)))

In [ ]:
# load model
model = load_model('model.h5')
# test on some training sequences
print('train')
evaluate_model(model, hindi_tokenizer, trainX, train)
# test on some test sequences
print('test')
evaluate_model(model, hindi_tokenizer, testX, test)

In [ ]:
INDIC_NLP_LIB_HOME

In [ ]:
INDIC_NLP_RESOURCES

In [ ]:
for path in sys.path:
    print (path)

In [ ]:
from indicnlp.normalize.indic_normalize import IndicNormalizerFactory

input_text="\u0958 \u0915\u093c"
remove_nuktas=False
factory=IndicNormalizerFactory()
normalizer=factory.get_normalizer("hi",remove_nuktas)
output_text=normalizer.normalize(input_text)

print(output_text)
print('Length before normalization: {}'.format(len(input_text)))
print('Length after normalization: {}'.format(len(output_text)))

In [ ]:
from indicnlp.normalize.indic_normalize import DevanagariNormalizer
input_text = "अत : इसे बिना टाँके वाला ऑपरेशन भी कहते हैं ।"
factory1=DevanagariNormalizer()
#normalizer1=factory1.get_normalizer("hi",remove_nuktas)
output_text1=factory1.normalize(input_text)
some = factory1.get_char_stats(input_text)
print (some)
print (input_text)
print(output_text1)
print('Length before normalization: {}'.format(len(input_text)))
print('Length after normalization: {}'.format(len(output_text1)))

In [ ]:
from indicnlp.transliterate.unicode_transliterate import UnicodeIndicTransliterator
input_text='राजस्थान'
# input_text='രാജസ്ഥാന'
# input_text='රාජස්ථාන'
print(UnicodeIndicTransliterator.transliterate(input_text,"hi","mr"))

In [ ]:
from indicnlp.tokenize import indic_tokenize  

indic_string='अनूप,अनूप?।फोन,'

print('Input String: {}'.format(indic_string))
print('Tokens: ')
a = list()
for t in indic_tokenize.trivial_tokenize(indic_string): 
    a.append(t)
print (a)


In [ ]:
from HindiTokenizer import Tokenizer

In [ ]:
t=Tokenizer("यह वाक्य हिन्दी में है।")